<a href="https://colab.research.google.com/github/YoniTint/trust-ai-project/blob/main/trustuworth_ml_project_variances.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


## Download data

In [ ]:
## CURRENTLY NOT TESTED YET SO DON'T USE!!
import requests
import zipfile
from pathlib import Path

# Setup path to a data folder
image_path = Path(r"/content/drive/MyDrive/Colab Notebooks/trustworthy_ml/data/data/celeba")

# If the image folder doesn't exist, download it and prepare it...
if not image_path.is_dir():
  print(f"{image_path} directory already exists... skipping download")
else:
  print(f"{image_path} does not exists, creating one...")
  image_path.mkdir(parents=True, exist_ok=True)

  # Unzip celeba data
  with zipfile.ZipFile("/content/drive/MyDrive/Colab Notebooks/trustworthy_ml/data/data/archive (1).zip", "r") as zip_ref:
    print("Unzipping celeba data...")
    zip_ref.extractall(image_path)

##Loading libraries##

In [ ]:
!pip install grad-cam
!pip install ultralytics

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 29.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for grad-cam: filename=grad_cam-1.4.8-py3-none-any.whl size=38243 sha256=f9e2f8e094bcd71bb6d5e751500f1f2eae48c0969fe025e2d583c10e86093c55
  Stored in directory: /root/.cache/pip/wheels/f8/04/36/94ff3c8a4215826a21946b34c01180817e606989fdf53f7cd6
Successfully built grad-cam
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 613.8/613.8 kB 7.2 MB/s eta 0:00:00


## Import Libraries

In [ ]:
import warnings
warnings.filterwarnings('ignore')
warnings.simplefilter('ignore')
import torch
import cv2
import numpy as np
import requests
import torchvision.transforms as transforms
from pytorch_grad_cam import EigenCAM
from pytorch_grad_cam.utils.image import show_cam_on_image, scale_cam_image
from PIL import Image
from google.colab.patches import cv2_imshow
from pathlib import Path
import os
import pandas as pd
from matplotlib import pyplot as plt

# Functions

In [ ]:
COLORS = np.random.uniform(0, 255, size=(80, 3))

def parse_detections(results):
    detections = results.pandas().xyxy[0]
    detections = detections.to_dict()
    boxes, colors, names = [], [], []

    for i in range(len(detections["xmin"])):
        confidence = detections["confidence"][i]
        if confidence < 0.2:
            continue
        xmin = int(detections["xmin"][i])
        ymin = int(detections["ymin"][i])
        xmax = int(detections["xmax"][i])
        ymax = int(detections["ymax"][i])
        name = detections["name"][i]
        category = int(detections["class"][i])
        color = COLORS[category]

        boxes.append((xmin, ymin, xmax, ymax))
        colors.append(color)
        names.append(name)
    return boxes, colors, names


def draw_detections(boxes, colors, names, img):
    for box, color, name in zip(boxes, colors, names):
        xmin, ymin, xmax, ymax = box
        cv2.rectangle(
            img,
            (xmin, ymin),
            (xmax, ymax),
            color,
            2)

        cv2.putText(img, name, (xmin, ymin - 5),
                    cv2.FONT_HERSHEY_SIMPLEX, 0.8, color, 2,
                    lineType=cv2.LINE_AA)
    return img

def preprocess_image(image_url, is_local_image=True, nm_imgs=1, index=1, metadata_df=None):
  if is_local_image:
    img = cv2.imread(image_url + '/' + metadata_df.sample(nm_imgs)["image_id"].values[index])
  else:
    img = np.array(Image.open(requests.get(image_url, stream=True).raw))
  img = cv2.resize(img, (640, 640)) # YOLO expects exactly 640 shape to work
  rgb_img = img.copy()
  img = np.float32(img) / 255
  transform = transforms.ToTensor()
  image_as_tensor = transform(img).unsqueeze(0)

  return image_as_tensor, rgb_img, img

def load_model(model_path, model_name):
  model = torch.hub.load(model_path, model_name, pretrained=True)
  model.eval()
  model.cpu()
  # Yolo need the one before the last, change for other models?
  target_layers = [model.model.model.model[-2]]

  return model, target_layers

def add_bboxes_to_image(model, rgb_img):
  results = model([rgb_img])
  boxes, colors, names = parse_detections(results)
  detections = draw_detections(boxes, colors, names, rgb_img.copy())

  return detections

def activate_grad_cam_on_image(model, target_layers, image_as_tensor, img):
  # Flags work for now, if configuration needed, will be not hardcoded
  cam = EigenCAM(model, target_layers, use_cuda=False)
  grayscale_cam = cam(image_as_tensor)[0, :, :]
  cam_image = show_cam_on_image(img, grayscale_cam, use_rgb=True)

  heatmap = cv2.applyColorMap(np.uint8(255 * grayscale_cam), colormap)
  heatmap = cv2.cvtColor(heatmap, cv2.COLOR_BGR2RGB)

  return cam_image, heatmap

In [ ]:
# INIT COLORMAP VARIABLE
colormap = cv2.COLORMAP_JET

##Results on a dataset##
Now we'll try to get results for a full data set. this dataset is taken from: https://datasets.activeloop.ai/docs/ml/datasets/celeba-dataset/.

In [ ]:
cd /content/drive/MyDrive/Colab Notebooks/trustworthy_ml/data

/content/drive/MyDrive/Colab Notebooks/trustworthy_ml/data


### Checking that dataset exists in the drive

In [ ]:
# How many images we will look on from the dataset
NM_IMGS = 1000

In [ ]:
BASIC_PATH = r"/content/drive/MyDrive/Colab Notebooks/trustworthy_ml/data/data/celeba"
FEATURE_PATH = os.path.join(BASIC_PATH,'list_attr_celeba.csv')
landmarks_PATH = os.path.join(BASIC_PATH,'list_landmarks_align_celeba.csv')
IMG_PATH = os.path.join(BASIC_PATH,'img_align_celeba/img_align_celeba')
pd.set_option('display.max_colwidth', None)

df = pd.read_csv(FEATURE_PATH, nrows=NM_IMGS + 2000)
landmarks_df = pd.read_csv(landmarks_PATH, nrows=NM_IMGS + 2000)
df.head()

image_id  5_o_Clock_Shadow  Arched_Eyebrows  Attractive  Bags_Under_Eyes  \
0  000001.jpg                -1                1           1               -1   
1  000002.jpg                -1               -1          -1                1   
2  000003.jpg                -1               -1          -1               -1   
3  000004.jpg                -1               -1           1               -1   
4  000005.jpg                -1                1           1               -1   

   Bald  Bangs  Big_Lips  Big_Nose  Black_Hair  ...  Sideburns  Smiling  \
0    -1     -1        -1        -1          -1  ...         -1        1   
1    -1     -1        -1         1          -1  ...         -1        1   
2    -1     -1         1        -1          -1  ...         -1       -1   
3    -1     -1        -1        -1          -1  ...         -1       -1   
4    -1     -1         1        -1          -1  ...         -1       -1   

   Straight_Hair  Wavy_Hair  Wearing_Earrings  Wearing_Hat  Wearing_Lipstick  \
0              1         -1                 1           -1                 1   
1             -1         -1                -1           -1                -1   
2             -1          1                -1           -1                -1   
3              1         -1                 1           -1                 1   
4             -1         -1                -1           -1                 1   

   Wearing_Necklace  Wearing_Necktie  Young  
0                -1               -1      1  
1                -1               -1      1  
2                -1               -1      1  
3                 1               -1      1  
4                -1               -1      1  

[5 rows x 41 columns]

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"

## Testing the model on the dataset

In [ ]:
from google.colab.patches import cv2_imshow
import pickle

outputs_folder = f"{BASIC_PATH}/img_align_celeba/img_align_celeba/outputs"

EPSILON = 1e-5
VARIANCES = [0.000001, 0.00001, 0.0001, 0.001, 0.01, 0.1]
#VARIANCES = [0.000001, 0.00001]
#VARIANCES = [0.01, 0.1]


for variance_index, variance in enumerate(VARIANCES):
  record_list = []
  for index in range(2000, 2000 + NM_IMGS):
      print(f'Variance #{variance_index + 4}: {variance}')
      print(f'Image #{index}')
      img = cv2.imread(IMG_PATH + '/' + df["image_id"].values[index])
      img = cv2.resize(img, (640, 640))
      rgb_img = img.copy()
      img = np.float32(img) / 255
      transform = transforms.ToTensor()
      tensor = transform(img).unsqueeze(0)

      model = torch.hub.load('ultralytics/yolov5', 'yolov5l', pretrained=True).to(device)
      model.eval()
      print(f'Is model on gpu? {next(model.parameters()).is_cuda}')
      #model.cpu()
      target_layers = [model.model.model.model[-2]]

      results = model([rgb_img])
      boxes, colors, names = parse_detections(results)
      detections = draw_detections(boxes, colors, names, rgb_img.copy())
      Image.fromarray(detections)
      cam = EigenCAM(model, target_layers, use_cuda=False)
      grayscale_cam = cam(tensor)[0, :, :]
      cam_image = show_cam_on_image(img, grayscale_cam, use_rgb=True)
      Image.fromarray(cam_image)
      colormap = cv2.COLORMAP_JET
      heatmap = cv2.applyColorMap(np.uint8(255 * grayscale_cam), colormap)
      heatmap = cv2.cvtColor(heatmap, cv2.COLOR_BGR2RGB)
      Image.fromarray(heatmap)
      max_iter = 3
      delta = torch.zeros(img.shape[0], img.shape[1], 3, dtype=torch.float64).to(device)

      eps = EPSILON
      delta = delta + variance * torch.randn(img.shape[0], img.shape[1], 3).to(device)  * 255
      # clip delta to be within [delta-eps, delta+eps]

      delta = torch.clamp(delta, delta-eps, delta + eps)
      # clip delta to be between 0 and 1
      # delta = torch.clamp(delta, 0, 1)
      delta[np.where(heatmap == 0)] = 0

      delta_img = cv2.applyColorMap(np.uint8(delta.to("cpu")), colormap)
      delta_img[np.where(heatmap == 0)] = 0
      Image.fromarray(delta_img)

      img = cv2.imread(IMG_PATH + '/' + df["image_id"].values[index])
      img = cv2.resize(img, (640, 640))
      rgb_img = img.copy()
      noisy = rgb_img + delta_img

      # give predictions on noisy image
      results = model([noisy])
      boxes, colors, names = parse_detections(results)
      detections = draw_detections(boxes, colors, names, noisy.copy())
      Image.fromarray(detections)

      if (len(boxes) == 0) or (not 'person' in names):
        # cv2.imwrite(f"{outputs_folder}/noisy_variance_{variance_index}_image_{index}.png", noisy)
        # cv2.imwrite(f"{outputs_folder}/detections_variance_{variance_index}_image_{index}.png", detections)
        record_list.append({ 'variance': variance, 'image_index': index, 'is_fooled': True })
      else:
        # cv2.imwrite(f"{outputs_folder}/noisy_variance_{variance_index}_image_{index}.png", noisy)
        # cv2.imwrite(f"{outputs_folder}/detections_variance_{variance_index}_image_{index}.png", detections)
        record_list.append({ 'variance': variance, 'image_index': index, 'is_fooled': False })

  # For Pickle
  print(f'Finished {NM_IMGS}, writing records to file')
  with open(f'{BASIC_PATH}/img_align_celeba/img_align_celeba/outputs/records/record_variance_{variance_index}_{NM_IMGS}_images.pkl', 'wb') as f:
    pickle.dump(record_list, f)

print("end")

Variance #4: 1e-06
Image #2000


Downloading: "https://github.com/ultralytics/yolov5/zipball/master" to /root/.cache/torch/hub/master.zip
requirements: Ultralytics requirement ['gitpython>=3.1.30'] not found, attempting AutoUpdate...
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 188.6/188.6 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 16.1 MB/s eta 0:00:00

requirements: AutoUpdate success ✅ 4.3s, installed 1 package: ['gitpython>=3.1.30']
requirements: ⚠️ Restart runtime or rerun command for updates to take effect

YOLOv5 🚀 2023-9-2 Python-3.10.12 torch-2.0.1+cu118 CUDA:0 (NVIDIA A100-SXM4-40GB, 40514MiB)

Fusing layers... 
YOLOv5l summary: 367 layers, 46533693 parameters, 0 gradients
Adding AutoShape... 


Is model on gpu? True
Variance #4: 1e-06
Image #2001


Using cache found in /root/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2023-9-2 Python-3.10.12 torch-2.0.1+cu118 CUDA:0 (NVIDIA A100-SXM4-40GB, 40514MiB)

Fusing layers... 
YOLOv5l summary: 367 layers, 46533693 parameters, 0 gradients
Adding AutoShape... 


Is model on gpu? True
Variance #4: 1e-06
Image #2002


...

Is model on gpu? True
Variance #9: 0.1
Image #2998


Using cache found in /root/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2023-9-2 Python-3.10.12 torch-2.0.1+cu118 CUDA:0 (NVIDIA A100-SXM4-40GB, 40514MiB)

Fusing layers... 
YOLOv5l summary: 367 layers, 46533693 parameters, 0 gradients
Adding AutoShape... 


Is model on gpu? True
Variance #9: 0.1
Image #2999


Using cache found in /root/.cache/torch/hub/ultralytics_yolov5_master
YOLOv5 🚀 2023-9-2 Python-3.10.12 torch-2.0.1+cu118 CUDA:0 (NVIDIA A100-SXM4-40GB, 40514MiB)

Fusing layers... 
YOLOv5l summary: 367 layers, 46533693 parameters, 0 gradients
Adding AutoShape... 


Is model on gpu? True
Finished 1000, writing records to file
end


In [ ]:
def print_records(loaded_records):
  # Verify that the list is loaded correctly
  for index, obj in enumerate(loaded_records):
      print(f'Record #{index}')
      print(f'Variance: {obj["variance"]}')
      print(f'Image Index: {obj["image_index"]}')
      print(f'Is fooled ? {obj["is_fooled"]}')
      print()

def evaluate_variance_results(loaded_records):
  count = 0

  for obj in loaded_records:
    if obj["is_fooled"]:
      count += 1

  return count / len(loaded_records)

In [ ]:
for i in range(6):
  # Load the list back from the pickle file.
  with open(f'{BASIC_PATH}/img_align_celeba/img_align_celeba/outputs/records/record_variance_{i}_{NM_IMGS}_images.pkl', 'rb') as f:
      loaded_records = pickle.load(f)

  print(f'Printing percentage for is_fooled / total, for Variance #{i}: {VARIANCES[i]}')
  print(evaluate_variance_results(loaded_records))

Printing percentage for is_fooled / total, for Variance #0: 1e-06
0.32
Printing percentage for is_fooled / total, for Variance #1: 1e-05
0.32
Printing percentage for is_fooled / total, for Variance #2: 0.0001
0.32
Printing percentage for is_fooled / total, for Variance #3: 0.001
0.339
Printing percentage for is_fooled / total, for Variance #4: 0.01
0.313
Printing percentage for is_fooled / total, for Variance #5: 0.1
0.324
